<a href="https://colab.research.google.com/github/IndiaTJohnson/Prediction-of-Product-Sales/blob/main/Project1_Part5_Core_IndiaJohnson.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Project 1 - Part 5 (Core)**

### **Imports**

In [1]:
#Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
pd.set_option('display.max_columns',100)
import missingno
from sklearn.model_selection import train_test_split
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder, OrdinalEncoder
from sklearn.pipeline import make_pipeline
from sklearn.impute import SimpleImputer
# Set pandas as the default output for sklearn
from sklearn import set_config
set_config(transform_output='pandas')

### **Configuration Settings**

In [2]:
## Display all columns
pd.set_option('display.max_column', None)

## Display all rows
pd.set_option('display.max_rows', None)

#SK Learn Display
set_config(display='diagram')

### **Load Data**

In [3]:
#Load in uncleaned data
fpath = "/content/drive/MyDrive/Coding Dojo/CodingDojo/02-IntroML/Week05/Data/sales_predictions_2023.csv"
df = pd.read_csv(fpath)

### **Perform EDA**

In [4]:
#Check the first 5 rows
df.head()

Item_Identifier  Item_Weight Item_Fat_Content  Item_Visibility  \
0           FDA15         9.30          Low Fat         0.016047   
1           DRC01         5.92          Regular         0.019278   
2           FDN15        17.50          Low Fat         0.016760   
3           FDX07        19.20          Regular         0.000000   
4           NCD19         8.93          Low Fat         0.000000   

               Item_Type  Item_MRP Outlet_Identifier  \
0                  Dairy  249.8092            OUT049   
1            Soft Drinks   48.2692            OUT018   
2                   Meat  141.6180            OUT049   
3  Fruits and Vegetables  182.0950            OUT010   
4              Household   53.8614            OUT013   

   Outlet_Establishment_Year Outlet_Size Outlet_Location_Type  \
0                       1999      Medium               Tier 1   
1                       2009      Medium               Tier 3   
2                       1999      Medium               Tier 1   
3                       1998         NaN               Tier 3   
4                       1987        High               Tier 3   

         Outlet_Type  Item_Outlet_Sales  
0  Supermarket Type1          3735.1380  
1  Supermarket Type2           443.4228  
2  Supermarket Type1          2097.2700  
3      Grocery Store           732.3800  
4  Supermarket Type1           994.7052

In [5]:
#Explore the data
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8523 entries, 0 to 8522
Data columns (total 12 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   Item_Identifier            8523 non-null   object 
 1   Item_Weight                7060 non-null   float64
 2   Item_Fat_Content           8523 non-null   object 
 3   Item_Visibility            8523 non-null   float64
 4   Item_Type                  8523 non-null   object 
 5   Item_MRP                   8523 non-null   float64
 6   Outlet_Identifier          8523 non-null   object 
 7   Outlet_Establishment_Year  8523 non-null   int64  
 8   Outlet_Size                6113 non-null   object 
 9   Outlet_Location_Type       8523 non-null   object 
 10  Outlet_Type                8523 non-null   object 
 11  Item_Outlet_Sales          8523 non-null   float64
dtypes: float64(4), int64(1), object(7)
memory usage: 799.2+ KB


In [6]:
#Check data types
df.dtypes

Item_Identifier               object
Item_Weight                  float64
Item_Fat_Content              object
Item_Visibility              float64
Item_Type                     object
Item_MRP                     float64
Outlet_Identifier             object
Outlet_Establishment_Year      int64
Outlet_Size                   object
Outlet_Location_Type          object
Outlet_Type                   object
Item_Outlet_Sales            float64
dtype: object

In [7]:
#Check for duplicate rows
df.duplicated().sum()

0

In [8]:
#Check for null values
df.isna().sum()

Item_Identifier                 0
Item_Weight                  1463
Item_Fat_Content                0
Item_Visibility                 0
Item_Type                       0
Item_MRP                        0
Outlet_Identifier               0
Outlet_Establishment_Year       0
Outlet_Size                  2410
Outlet_Location_Type            0
Outlet_Type                     0
Item_Outlet_Sales               0
dtype: int64

**We will deal with the missing values in the next step with SimpleImputer.**

In [9]:
#Check for inconsistant categories

#Create variable for string columns
string_cols = df.select_dtypes("object").columns

# Obtain the value counts for all string columns
for col in string_cols:
  print(f"Value Counts for {col}")
  print(df[col].value_counts())
  # Increasing readability by adding an empty line
  print('\n')


Value Counts for Item_Identifier
FDW13    10
FDG33    10
NCY18     9
FDD38     9
DRE49     9
FDV60     9
NCQ06     9
FDF52     9
FDX04     9
NCJ30     9
FDV38     9
NCF42     9
FDT07     9
FDW26     9
NCL31     9
FDU12     9
FDG09     9
FDQ40     9
FDX20     9
NCI54     9
FDX31     9
FDP25     9
FDW49     9
FDF56     9
FDO19     9
DRN47     9
NCB18     9
FDE11     8
NCX05     8
FDQ39     8
FDT55     8
FDO32     8
FDT40     8
FDZ20     8
FDH27     8
FDY49     8
FDS33     8
FDR04     8
FDR43     8
FDR59     8
FDJ55     8
FDT24     8
FDY55     8
FDV09     8
FDU23     8
FDY47     8
DRD25     8
FDK58     8
FDL58     8
FDX58     8
FDR44     8
FDP28     8
FDA39     8
FDH28     8
DRF27     8
FDX21     8
FDY56     8
FDF05     8
FDL20     8
FDY03     8
NCK05     8
FDS55     8
DRA59     8
FDG24     8
NCE54     8
FDZ21     8
FDA04     8
FDW24     8
FDT49     8
DRF23     8
FDD05     8
FDH10     8
FDX50     8
FDT32     8
FDK20     8
FDU13     8
FDN56     8
FDZ26     8
FDL34     8
DRF01     8
FDG38  

In [10]:
#Change High to Large in Outlet_Size
df["Outlet_Size"] = df["Outlet_Size"].replace({'High':'Large'})
df['Outlet_Size'].value_counts()

Medium    2793
Small     2388
Large      932
Name: Outlet_Size, dtype: int64

In [11]:
#Make Low fat and Regular categories consistant
df['Item_Fat_Content'] = df['Item_Fat_Content'].replace({'LF': 'Low Fat', 'low fat': 'Low Fat', 'reg': 'Regular'})
df['Item_Fat_Content'].value_counts()

Low Fat    5517
Regular    3006
Name: Item_Fat_Content, dtype: int64

In [12]:
#Check numerical values for inconsistent values
df.describe().round(2)

Item_Weight  Item_Visibility  Item_MRP  Outlet_Establishment_Year  \
count      7060.00          8523.00   8523.00                    8523.00   
mean         12.86             0.07    140.99                    1997.83   
std           4.64             0.05     62.28                       8.37   
min           4.56             0.00     31.29                    1985.00   
25%           8.77             0.03     93.83                    1987.00   
50%          12.60             0.05    143.01                    1999.00   
75%          16.85             0.09    185.64                    2004.00   
max          21.35             0.33    266.89                    2009.00   

       Item_Outlet_Sales  
count            8523.00  
mean             2181.29  
std              1706.50  
min                33.29  
25%               834.25  
50%              1794.33  
75%              3101.30  
max             13086.96

### **Seperate the Data**

In [13]:
#Seperate the target value and features
target = 'Item_Outlet_Sales'
X = df.drop(columns=[target, 'Item_Identifier'])
y = df[target]

In [14]:
X

Item_Weight Item_Fat_Content  Item_Visibility              Item_Type  \
0           9.300          Low Fat         0.016047                  Dairy   
1           5.920          Regular         0.019278            Soft Drinks   
2          17.500          Low Fat         0.016760                   Meat   
3          19.200          Regular         0.000000  Fruits and Vegetables   
4           8.930          Low Fat         0.000000              Household   
5          10.395          Regular         0.000000           Baking Goods   
6          13.650          Regular         0.012741            Snack Foods   
7             NaN          Low Fat         0.127470            Snack Foods   
8          16.200          Regular         0.016687           Frozen Foods   
9          19.200          Regular         0.094450           Frozen Foods   
10         11.800          Low Fat         0.000000  Fruits and Vegetables   
11         18.500          Regular         0.045464                  Dairy   
12         15.100          Regular         0.100014  Fruits and Vegetables   
13         17.600          Regular         0.047257            Snack Foods   
14         16.350          Low Fat         0.068024  Fruits and Vegetables   
15          9.000          Regular         0.069089              Breakfast   
16         11.800          Low Fat         0.008596     Health and Hygiene   
17          9.000          Regular         0.069196              Breakfast   
18            NaN          Low Fat         0.034238            Hard Drinks   
19         13.350          Low Fat         0.102492                  Dairy   
20         18.850          Regular         0.138190            Snack Foods   
21            NaN          Regular         0.035400           Baking Goods   
22         14.600          Low Fat         0.025698              Household   
23            NaN          Low Fat         0.057557           Baking Goods   
24         13.850          Regular         0.025896           Frozen Foods   
25         13.000          Low Fat         0.099887              Household   
26          7.645          Regular         0.066693            Snack Foods   
27         11.650          Low Fat         0.019356            Hard Drinks   
28          5.925          Regular         0.161467                  Dairy   
29            NaN          Regular         0.072222                 Canned   
30         19.250          Low Fat         0.170349                  Dairy   
31         18.600          Low Fat         0.080829     Health and Hygiene   
32         18.700          Low Fat         0.000000            Snack Foods   
33         17.850          Low Fat         0.000000                 Breads   
34         17.500          Low Fat         0.097904            Soft Drinks   
35         10.000          Low Fat         0.089291     Health and Hygiene   
36            NaN          Regular         0.059512  Fruits and Vegetables   
37          8.850          Regular         0.113124            Soft Drinks   
38            NaN          Regular         0.123111            Snack Foods   
39            NaN          Low Fat         0.026481            Snack Foods   
40         13.350          Low Fat         0.102512                  Dairy   
41          9.800          Low Fat         0.026818                   Meat   
42         13.600          Low Fat         0.117818            Snack Foods   
43         21.350          Low Fat         0.069103                 Canned   
44         12.150          Regular         0.042278                 Canned   
45          6.420          Low Fat         0.089499                  Dairy   
46         19.600          Low Fat         0.000000     Health and Hygiene   
47         10.000          Low Fat         0.025880                 Canned   
48         15.850          Regular         0.121633           Baking Goods   
49            NaN          Regular         0.255395                  Dairy   
50          7.390          L

### **Train Test Split**

In [15]:
#Train test split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = .30, random_state = 42)

### **Create Pipelines**

In [16]:
#Check columns with missing values
df.isna().sum()

Item_Identifier                 0
Item_Weight                  1463
Item_Fat_Content                0
Item_Visibility                 0
Item_Type                       0
Item_MRP                        0
Outlet_Identifier               0
Outlet_Establishment_Year       0
Outlet_Size                  2410
Outlet_Location_Type            0
Outlet_Type                     0
Item_Outlet_Sales               0
dtype: int64

In [17]:
df["Item_Weight"].describe().round(2)

count    7060.00
mean       12.86
std         4.64
min         4.56
25%         8.77
50%        12.60
75%        16.85
max        21.35
Name: Item_Weight, dtype: float64

In [18]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8523 entries, 0 to 8522
Data columns (total 12 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   Item_Identifier            8523 non-null   object 
 1   Item_Weight                7060 non-null   float64
 2   Item_Fat_Content           8523 non-null   object 
 3   Item_Visibility            8523 non-null   float64
 4   Item_Type                  8523 non-null   object 
 5   Item_MRP                   8523 non-null   float64
 6   Outlet_Identifier          8523 non-null   object 
 7   Outlet_Establishment_Year  8523 non-null   int64  
 8   Outlet_Size                6113 non-null   object 
 9   Outlet_Location_Type       8523 non-null   object 
 10  Outlet_Type                8523 non-null   object 
 11  Item_Outlet_Sales          8523 non-null   float64
dtypes: float64(4), int64(1), object(7)
memory usage: 799.2+ KB


In [19]:
#Create Ordinal pipeline: Create list, OrdinalEncoder, and tuple

#Variable of ordinal columns
ordinal_cols = ['Outlet_Location_Type', 'Outlet_Size']

#Ordered Category Lists
location_type_list = ['Tier 1', 'Tier 2', 'Tier 3']
size_list = ['Small', 'Medium', 'Large']

#Transformers
ord = OrdinalEncoder(categories=[location_type_list, size_list])
freq_imputer = SimpleImputer(strategy='most_frequent')

#Scaler
scaler = StandardScaler()

#Pipeline
ord_pipeline = make_pipeline(freq_imputer, ord, scaler)

#Tuple
ord_tuple = ('ordinal', ord_pipeline, ordinal_cols)

In [20]:
#Create categorical pipeline: Create list, OneHotEncoder, and tuple

#Variable of categorical columns
cat_cols = X_train.select_dtypes('object').drop(columns=ordinal_cols).columns

#Transformers
missing_imputer = SimpleImputer(strategy='constant', fill_value='missing')
ohe = OneHotEncoder(sparse_output = False, handle_unknown = 'ignore')

#Pipeline
cat_pipeline = make_pipeline(missing_imputer, ohe)

#Tuple
ohe_tuple = ('categorical', cat_pipeline, cat_cols)

In [21]:
#Create numerical pipeline: Create list, StandardSclaer, SimpleImputer for Item_Weight, and tuple

#Create numerical columns variable
num_cols = X_train.select_dtypes('number').columns

#Transformers
mean_imputer = SimpleImputer(strategy='mean')
scaler2 = StandardScaler()

#Pipeline
num_pipeline = make_pipeline(mean_imputer, scaler2)

#Tuple
num_tuple = ('numeric', num_pipeline, num_cols)

### **Create ColumnTransformer**

In [22]:
col_transformer = ColumnTransformer([ord_tuple,
                                    ohe_tuple,
                                    num_tuple],
                                    remainder = 'drop',
                                    verbose_feature_names_out=False)

In [23]:
col_transformer

ColumnTransformer(transformers=[('ordinal',
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer(strategy='most_frequent')),
                                                 ('ordinalencoder',
                                                  OrdinalEncoder(categories=[['Tier '
                                                                              '1',
                                                                              'Tier '
                                                                              '2',
                                                                              'Tier '
                                                                              '3'],
                                                                             ['Small',
                                                                              'Medium',
                                                                              'Large']])),
                                                 ('standardscaler',
                                                  StandardScaler())]),
                                 ['Outlet_Location_Type', 'Outlet_Size']),
                                ('categorical',
                                 Pipeline(steps=[('simpleimputer',...
                                                  OneHotEncoder(handle_unknown='ignore',
                                                                sparse=False))]),
                                 Index(['Item_Fat_Content', 'Item_Type', 'Outlet_Identifier', 'Outlet_Type'], dtype='object')),
                                ('numeric',
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer()),
                                                 ('standardscaler',
                                                  StandardScaler())]),
                                 Index(['Item_Weight', 'Item_Visibility', 'Item_MRP',
       'Outlet_Establishment_Year'],
      dtype='object'))],
                  verbose_feature_names_out=False)

### **Fit the Training Data**

In [24]:
#Fit the ColumnTransformer on the training data
col_transformer.fit(X_train)

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_encoders.py:868: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


ColumnTransformer(transformers=[('ordinal',
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer(strategy='most_frequent')),
                                                 ('ordinalencoder',
                                                  OrdinalEncoder(categories=[['Tier '
                                                                              '1',
                                                                              'Tier '
                                                                              '2',
                                                                              'Tier '
                                                                              '3'],
                                                                             ['Small',
                                                                              'Medium',
                                                                              'Large']])),
                                                 ('standardscaler',
                                                  StandardScaler())]),
                                 ['Outlet_Location_Type', 'Outlet_Size']),
                                ('categorical',
                                 Pipeline(steps=[('simpleimputer',...
                                                  OneHotEncoder(handle_unknown='ignore',
                                                                sparse=False))]),
                                 Index(['Item_Fat_Content', 'Item_Type', 'Outlet_Identifier', 'Outlet_Type'], dtype='object')),
                                ('numeric',
                                 Pipeline(steps=[('simpleimputer',
                                                  SimpleImputer()),
                                                 ('standardscaler',
                                                  StandardScaler())]),
                                 Index(['Item_Weight', 'Item_Visibility', 'Item_MRP',
       'Outlet_Establishment_Year'],
      dtype='object'))],
                  verbose_feature_names_out=False)

### **Transform the Training and Test Data**

In [27]:
#Create variables of processed/transformed data
X_train_processed = col_transformer.transform(X_train)

X_test_processed = col_transformer.transform(X_test)

### **Check the Data**

In [28]:
X_train_processed.head()

Outlet_Location_Type  Outlet_Size  Item_Fat_Content_Low Fat  \
1921              1.083627     0.284752                       0.0   
655              -1.383428    -1.384039                       1.0   
2229              1.083627     0.284752                       0.0   
2537             -0.149901     0.284752                       1.0   
3528              1.083627     1.953543                       0.0   

      Item_Fat_Content_Regular  Item_Type_Baking Goods  Item_Type_Breads  \
1921                       1.0                     0.0               0.0   
655                        0.0                     0.0               0.0   
2229                       1.0                     0.0               1.0   
2537                       0.0                     0.0               0.0   
3528                       1.0                     0.0               0.0   

      Item_Type_Breakfast  Item_Type_Canned  Item_Type_Dairy  \
1921                  0.0               0.0              0.0   
655                   0.0               0.0              0.0   
2229                  0.0               0.0              0.0   
2537                  0.0               0.0              0.0   
3528                  0.0               0.0              0.0   

      Item_Type_Frozen Foods  Item_Type_Fruits and Vegetables  \
1921                     0.0                              1.0   
655                      0.0                              0.0   
2229                     0.0                              0.0   
2537                     0.0                              0.0   
3528                     1.0                              0.0   

      Item_Type_Hard Drinks  Item_Type_Health and Hygiene  \
1921                    0.0                           0.0   
655                     0.0                           0.0   
2229                    0.0                           0.0   
2537                    0.0                           0.0   
3528                    0.0                           0.0   

      Item_Type_Household  Item_Type_Meat  Item_Type_Others  \
1921                  0.0             0.0               0.0   
655                   1.0             0.0               0.0   
2229                  0.0             0.0               0.0   
2537                  0.0             0.0               0.0   
3528                  0.0             0.0               0.0   

      Item_Type_Seafood  Item_Type_Snack Foods  Item_Type_Soft Drinks  \
1921                0.0                    0.0                    0.0   
655                 0.0                    0.0                    0.0   
2229                0.0                    0.0                    0.0   
2537                0.0                    1.0                    0.0   
3528                0.0                    0.0                    0.0   

      Item_Type_Starchy Foods  Outlet_Identifier_OUT010  \
1921                      0.0                       1.0   
655                       0.0                       0.0   
2229                      0.0                       0.0   
2537                      0.0                       0.0   
3528                      0.0                       0.0   

      Outlet_Identifier_OUT013  Outlet_Identifier_OUT017  \
1921                       0.0                       0.0   
655                        0.0                       0.0   
2229                       0.0                       0.0   
2537                       0.0                       0.0   
3528                       1.0                       0.0   

      Outlet_Identifier_OUT018  Outlet_Identifier_OUT019  \
1921                       0.0                       0.0   
655                        0.0                       0.0   
2229                       0.0                       0.0   
2537                       0.0                       0.0   
3528                       0.0                       0.0   

      Outlet_Identifier_OUT027  Outlet_Identifier_OUT035  \
1921                       0.0      

In [29]:
X_test_processed.head()

Outlet_Location_Type  Outlet_Size  Item_Fat_Content_Low Fat  \
7503              1.083627     1.953543                       1.0   
2957             -1.383428    -1.384039                       1.0   
7031             -1.383428     0.284752                       0.0   
1084              1.083627     0.284752                       0.0   
856              -0.149901    -1.384039                       0.0   

      Item_Fat_Content_Regular  Item_Type_Baking Goods  Item_Type_Breads  \
7503                       0.0                     0.0               0.0   
2957                       0.0                     0.0               0.0   
7031                       1.0                     0.0               0.0   
1084                       1.0                     0.0               0.0   
856                        1.0                     0.0               0.0   

      Item_Type_Breakfast  Item_Type_Canned  Item_Type_Dairy  \
7503                  0.0               0.0              0.0   
2957                  0.0               0.0              0.0   
7031                  0.0               1.0              0.0   
1084                  0.0               0.0              0.0   
856                   0.0               0.0              0.0   

      Item_Type_Frozen Foods  Item_Type_Fruits and Vegetables  \
7503                     1.0                              0.0   
2957                     0.0                              0.0   
7031                     0.0                              0.0   
1084                     0.0                              0.0   
856                      0.0                              0.0   

      Item_Type_Hard Drinks  Item_Type_Health and Hygiene  \
7503                    0.0                           0.0   
2957                    0.0                           1.0   
7031                    0.0                           0.0   
1084                    0.0                           0.0   
856                     0.0                           0.0   

      Item_Type_Household  Item_Type_Meat  Item_Type_Others  \
7503                  0.0             0.0               0.0   
2957                  0.0             0.0               0.0   
7031                  0.0             0.0               0.0   
1084                  0.0             0.0               0.0   
856                   0.0             1.0               0.0   

      Item_Type_Seafood  Item_Type_Snack Foods  Item_Type_Soft Drinks  \
7503                0.0                    0.0                    0.0   
2957                0.0                    0.0                    0.0   
7031                0.0                    0.0                    0.0   
1084                0.0                    0.0                    1.0   
856                 0.0                    0.0                    0.0   

      Item_Type_Starchy Foods  Outlet_Identifier_OUT010  \
7503                      0.0                       0.0   
2957                      0.0                       0.0   
7031                      0.0                       0.0   
1084                      0.0                       0.0   
856                       0.0                       0.0   

      Outlet_Identifier_OUT013  Outlet_Identifier_OUT017  \
7503                       1.0                       0.0   
2957                       0.0                       0.0   
7031                       0.0                       0.0   
1084                       0.0                       0.0   
856                        0.0                       0.0   

      Outlet_Identifier_OUT018  Outlet_Identifier_OUT019  \
7503                       0.0                       0.0   
2957                       0.0                       0.0   
7031                       0.0                       0.0   
1084                       0.0                       0.0   
856                        0.0                       0.0   

      Outlet_Identifier_OUT027  Outlet_Identifier_OUT035  \
7503                       0.0      